In [1]:
import requests
import pandas as pd
from datetime import datetime
from tqdm import tqdm

BINANCE_CANDLE_COLUMNS = ['opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime',
                          'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

def binance_recursive_fetch_2(coins, interval, starttime, endtime, data_type='spot'):
    all_coins_result = {}
    data_list = []
    call_dict = {}
    
    for coin in tqdm(coins):
        result_list = []
        current_time = starttime
        call = 0
        timestamps = []
        
        while current_time < endtime:
            if ((int((endtime - current_time) / (1000 * 60))) + 1) >= 1000:
                limit = 1000
            else:
                limit = int((endtime - current_time) / (1000 * 60) + 1)
            
            if data_type == 'spot':
                url = (f'https://api.binance.com/api/v3/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            elif data_type == 'futures':
                url = (f'https://fapi.binance.com/fapi/v1/klines'
                       f'?symbol={coin}USDT'
                       f'&startTime={str(current_time)}'
                       f'&interval={interval}'
                       f'&limit={str(limit)}')
            
            result_list += requests.get(url).json()
            
            if result_list:
                # Update current_time with the timestamp of the last data point fetched, plus 1 minute (60000 ms)
                current_time = result_list[-1][0] + 60000
                timestamps.append(current_time)
                call += 1
                
                # Check if the last fetched timestamp is greater than or equal to endtime
                if current_time >= endtime:
                    print(f"Reached endtime at {datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')}. Stopping fetch.")
                    break
                
                print((datetime.fromtimestamp(current_time / 1000).strftime('%Y-%m-%d %H:%M:%S')) + 
                      f' status : {current_time < endtime}, time : {current_time}, limit : {call * 2}')
            
            # Ensure there's no continuous fetching of the same timestamp
            if len(timestamps) > 1 and timestamps[-1] == timestamps[-2]:
                print("Duplicate timestamp detected. Stopping fetch.")
                break
            
            # Sleep if needed to avoid rate limiting (adjust based on your rate limit)
            # time.sleep(0.1)  # Uncomment if needed
            
        current_df = pd.DataFrame(result_list, columns=BINANCE_CANDLE_COLUMNS)
        current_df['coin'] = coin
        current_df = current_df[['coin'] + BINANCE_CANDLE_COLUMNS]
        current_df = current_df.values.tolist()
        
        data_list += current_df
        call_dict.update({coin: call})
    
    return {'data': data_list, 'call': call_dict}

# Set endtime to the current time (today)
endtime = int(datetime.utcnow().timestamp() * 1000)

# # Example usage with today's date as the end time
# sample_spot = binance_recursive_fetch_2(
#     ['USDT'],
#     '1m',
#     starttime=int(pd.to_datetime('2023-01-01 00:00', utc=True).timestamp() * 1000),
#     endtime=endtime,
#     data_type='spot'  # Fetch spot data
# )

# print(sample_spot['data'])

In [2]:
# Fetch NEAR USDT
sample_spot = binance_recursive_fetch_2(
    ['ATOM'],
    '1h',
    starttime=int(pd.to_datetime('2020-01-01 00:00', utc=True).timestamp() * 1000),
    endtime=endtime,
    data_type='futures'  # Fetch spot data
)

print(sample_spot['data'])

  0%|          | 0/1 [00:00<?, ?it/s]

2020-03-20 03:01:00 status : True, time : 1584673260000, limit : 2
2020-04-30 19:01:00 status : True, time : 1588273260000, limit : 4
2020-06-11 11:01:00 status : True, time : 1591873260000, limit : 6
2020-07-23 03:01:00 status : True, time : 1595473260000, limit : 8
2020-09-02 19:01:00 status : True, time : 1599073260000, limit : 10
2020-10-14 11:01:00 status : True, time : 1602673260000, limit : 12
2020-11-25 03:01:00 status : True, time : 1606273260000, limit : 14
2021-01-05 19:01:00 status : True, time : 1609873260000, limit : 16
2021-02-16 11:01:00 status : True, time : 1613473260000, limit : 18
2021-03-30 03:01:00 status : True, time : 1617073260000, limit : 20
2021-05-10 19:01:00 status : True, time : 1620673260000, limit : 22
2021-06-21 11:01:00 status : True, time : 1624273260000, limit : 24
2021-08-02 03:01:00 status : True, time : 1627873260000, limit : 26
2021-09-12 19:01:00 status : True, time : 1631473260000, limit : 28
2021-10-24 11:01:00 status : True, time : 1635073260

100%|██████████| 1/1 [00:07<00:00,  7.40s/it]

[['ATOM', 1581076800000, '4.574', '4.870', '4.573', '4.610', '78089.77', 1581080399999, '364120.05238', 681, '50177.14', '234729.05257', '0'], ['ATOM', 1581080400000, '4.614', '4.700', '4.610', '4.690', '51144.09', 1581083999999, '238195.83372', 819, '28136.38', '131144.06818', '0'], ['ATOM', 1581084000000, '4.685', '4.870', '4.658', '4.839', '141139.71', 1581087599999, '671611.04718', 3167, '83826.46', '398902.32609', '0'], ['ATOM', 1581087600000, '4.838', '4.895', '4.775', '4.886', '232846.70', 1581091199999, '1125741.61715', 2313, '71249.95', '345119.48388', '0'], ['ATOM', 1581091200000, '4.874', '4.909', '4.782', '4.815', '139251.61', 1581094799999, '675046.18724', 2486, '61212.84', '297405.07922', '0'], ['ATOM', 1581094800000, '4.813', '4.906', '4.809', '4.868', '75221.57', 1581098399999, '366076.50344', 1980, '41384.04', '201436.15366', '0'], ['ATOM', 1581098400000, '4.869', '4.888', '4.838', '4.862', '45429.74', 1581101999999, '221055.88022', 899, '20153.88', '98163.47840', '0']

In [3]:
# Define the column names for the DataFrame based on the Binance API response structure
columns = ['coin', 'opentime', 'openprice', 'highprice', 'lowprice', 'closeprice', 'volume', 'closetime', 
           'quotevolume', 'trades', 'taker_buy_volume', 'taker_buy_quote', 'unused']

# Convert the list of data into a DataFrame
df = pd.DataFrame(sample_spot['data'], columns=columns)

# Show the first few rows of the DataFrame
df

coin       opentime openprice highprice lowprice closeprice     volume  \
0      ATOM  1581076800000     4.574     4.870    4.573      4.610   78089.77   
1      ATOM  1581080400000     4.614     4.700    4.610      4.690   51144.09   
2      ATOM  1581084000000     4.685     4.870    4.658      4.839  141139.71   
3      ATOM  1581087600000     4.838     4.895    4.775      4.886  232846.70   
4      ATOM  1581091200000     4.874     4.909    4.782      4.815  139251.61   
...     ...            ...       ...       ...      ...        ...        ...   
42553  ATOM  1734267600000     9.054     9.212    9.000      9.172  860635.63   
42554  ATOM  1734271200000     9.173     9.308    9.172      9.233  907825.15   
42555  ATOM  1734274800000     9.233     9.255    9.133      9.190  528154.00   
42556  ATOM  1734278400000     9.190     9.223    9.068      9.088  802355.70   
42557  ATOM  1734282000000     9.088     9.110    9.040      9.106  193400.62   

           closetime    quotevolume  trades taker_buy_volume taker_buy_quote  \
0      1581080399999   364120.05238     681         50177.14    234729.05257   
1      1581083999999   238195.83372     819         28136.38    131144.06818   
2      1581087599999   671611.04718    3167         83826.46    398902.32609   
3      1581091199999  1125741.61715    2313         71249.95    345119.48388   
4      1581094799999   675046.18724    2486         61212.84    297405.07922   
...              ...            ...     ...              ...             ...   
42553  1734271199999  7846636.63804   33948        429163.43   3913094.11421   
42554  1734274799999  8399720.15779   32356        446148.32   4128727.44522   
42555  1734278399999  4856080.30716   21516        274433.03   2523687.12151   
42556  1734281999999  7328596.83004   25741        371163.76   3389462.11363   
42557  1734285599999  1754897.02774    6489        113217.96   1027661.29975   

      unused  
0          0  
1          0  
2          0  
3          0  
4          0  
...      ...  
42553      0  
42554      0  
42555      0  
42556      0  
42557      0  

[42558 rows x 13 columns]

In [4]:
df.to_csv('ATOM_USDT_futures_data_2020.csv', index=False)

print("DataFrame has been saved to csv")

DataFrame has been saved to csv
